In [28]:
import numpy as np

import pandas as pd

import astropy

from astropy.timeseries import TimeSeries
from astropy.table import Table
from astropy import units as u

import plotly.graph_objects as go

from scipy.signal import find_peaks, peak_widths

import lightkurve as lk

import itertools 

From senior experience paper: KIC 4840672, KIC 8162789, KIC 8631751, and KIC 11100170

In [29]:
search_result_lc = lk.search_lightcurve("KIC 8162789")
lc_collection = search_result_lc[search_result_lc.author == "Kepler"].download_all()
# want short exposure times https://www.ut.edu/uploadedFiles/Academics/Acta_Spartae/AS_0601p1Argentieri.pdf

In [30]:
search_result_lc

SearchResult containing 17 data products.

 #       mission      year author exptime  target_name  distance
                                     s                   arcsec 
--- ----------------- ---- ------ ------- ------------- --------
  0 Kepler Quarter 01 2009 Kepler    1800 kplr008162789      0.0
  1 Kepler Quarter 02 2009 Kepler    1800 kplr008162789      0.0
  2 Kepler Quarter 03 2009 Kepler    1800 kplr008162789      0.0
  3 Kepler Quarter 04 2010 Kepler    1800 kplr008162789      0.0
  4 Kepler Quarter 05 2010 Kepler    1800 kplr008162789      0.0
  5 Kepler Quarter 06 2010 Kepler    1800 kplr008162789      0.0
  6 Kepler Quarter 07 2010 Kepler    1800 kplr008162789      0.0
  7 Kepler Quarter 10 2011 Kepler    1800 kplr008162789      0.0
  8 Kepler Quarter 09 2011 Kepler    1800 kplr008162789      0.0
  9 Kepler Quarter 08 2011 Kepler    1800 kplr008162789      0.0
 10 Kepler Quarter 11 2012 Kepler    1800 kplr008162789      0.0
 11 Kepler Quarter 12 2012 Kepler    1800 kplr008162789      0.0
 12 Kepler Quarter 13 2012 Kepler    1800 kplr008162789      0.0
 13 Kepler Quarter 14 2012 Kepler    1800 kplr008162789      0.0
 14 Kepler Quarter 15 2013 Kepler    1800 kplr008162789      0.0
 15 Kepler Quarter 16 2013 Kepler    1800 kplr008162789      0.0
 16 Kepler Quarter 17 2013 Kepler    1800 kplr008162789      0.0

According to this [link](https://www.ut.edu/uploadedFiles/Academics/Acta_Spartae/AS_0601p1Argentieri.pdf), we want short exposure times. I am building of these two tutorials: [one](http://docs.lightkurve.org/tutorials/3-science-examples/exoplanets-identifying-transiting-planet-signals.html) and [two](https://docs.lightkurve.org/tutorials/3-science-examples/periodograms-creating-periodograms.html#3.-Using-a-Kepler-Periodogram-to-Identify-a-Significant-Period)

In [88]:
def lightcurve_data(data):

    SAP=[]
    PDCSAP=[]
    norm=[]
    time=[]

    for x in range(0, len(data)-1):
        sap_ind=data[x]['sap_flux'].to_value().tolist()
        pdcsap_ind=data[x]['flux'].to_value().tolist() # source of the flux in the table is PDCSAP FLUX
        norm_ind=data[x].normalize()['flux'].to_value().tolist()
        time_ind=data[x]['time'].to_value('bkjd').tolist()

        SAP.append(sap_ind)
        PDCSAP.append(pdcsap_ind)
        norm.append(norm_ind)
        time.append(time_ind)
    
    stitched=lc_collection.stitch()
    quality_index = np.where(stitched['quality'] == 0)[0]
    stitched=stitched[quality_index]
    fully_norm_flux=stitched['flux'].to_value().tolist() 
    full_time=stitched['time'].to_value('bkjd').tolist()
    return(PDCSAP, SAP, norm, time, fully_norm_flux, full_time, stitched) 


Simple Aperture Photometry = SAP

Pre-search Data Conditioning SAP flux = PDCSAP

More info can be found [here](https://heasarc.gsfc.nasa.gov/docs/tess/LightCurveFile-Object-Tutorial.html)

In [89]:
test1=lightcurve_data(lc_collection)

In [90]:
stitched=test1[6].to_pandas().reset_index() 
stitched.head()

time      flux  flux_err  quality  timecorr  centroid_col  \
0  131.512361  1.000251  0.000309        0  0.001367    946.348313   
1  131.532795  0.999066  0.000310        0  0.001368    946.348415   
2  131.553230  0.999567  0.000310        0  0.001369    946.348387   
3  131.573664  0.999186  0.000310        0  0.001369    946.348763   
4  131.614533  1.000135  0.000310        0  0.001371    946.348462   

   centroid_row  cadenceno      sap_flux  sap_flux_err  ...  psf_centr1  \
0    744.178713       1105  30272.640625      5.515941  ...         NaN   
1    744.178383       1106  30249.880859      5.514870  ...         NaN   
2    744.178306       1107  30259.439453      5.515183  ...         NaN   
3    744.178038       1108  30255.339844      5.515021  ...         NaN   
4    744.178753       1110  30271.984375      5.515874  ...         NaN   

   psf_centr1_err  psf_centr2  psf_centr2_err  mom_centr1  mom_centr1_err  \
0             NaN         NaN             NaN  946.348313        0.000162   
1             NaN         NaN             NaN  946.348415        0.000162   
2             NaN         NaN             NaN  946.348387        0.000162   
3             NaN         NaN             NaN  946.348763        0.000162   
4             NaN         NaN             NaN  946.348462        0.000162   

   mom_centr2  mom_centr2_err  pos_corr1  pos_corr2  
0  744.178713        0.000176   0.006420  -0.011367  
1  744.178383        0.000177   0.006408  -0.011347  
2  744.178306        0.000177   0.006234  -0.011444  
3  744.178038        0.000177   0.006103  -0.011413  
4  744.178753        0.000176   0.006280  -0.010913  

[5 rows x 25 columns]

In [91]:
test1[5]

[131.51236078861984,
 131.53279530771397,
 131.5532297268146,
 131.5736640457908,
 131.61453298364358,
 131.63496730239422,
 131.65540172113833,
 131.69627065840177,
 131.73713939532172,
 131.75757391371735,
 131.77800823200232,
 131.79844265017164,
 131.81887716833444,
 131.839311486503,
 131.85974590443948,
 131.8801803223687,
 131.90061474030517,
 131.92104915812524,
 131.94148357582162,
 131.96191799340886,
 131.9823524109961,
 132.00278682857606,
 132.0232211459297,
 132.0436556634013,
 132.064090080632,
 132.10495881499082,
 132.1253933321059,
 132.1458276491103,
 132.16626206599904,
 132.18669658288127,
 132.2071309996536,
 132.24799973296467,
 132.26843424961407,
 132.2888685660364,
 132.3093029824522,
 132.35017181506555,
 132.37060623137222,
 132.39104064743879,
 132.41147506351263,
 132.43190947946277,
 132.47277841114555,
 132.4932127269858,
 132.53408145819412,
 132.5545159737958,
 132.57495038917114,
 132.59538470454572,
 132.61581921992183,
 132.6362536351735,
 132.65668

In [92]:
len(test1)

7

In [93]:
def lightcurve_traces(data):
    upper_range=len(data)-1

    data2plot=lightcurve_data(data)

    SAP_traces={}
    PDCSAP_traces={}
    norm_traces={}
    
    fully_norm_flux_trace=go.Scattergl(x=data2plot[5], y=data2plot[4],  mode='markers',  marker_size=1)

    for x in range(0, upper_range):
        SAP_traces['SAP_trace_' + str(x)]=go.Scattergl(x=data2plot[3][x], name=f"Quarter {lc_collection[x].quarter}", y=data2plot[1][x], mode='markers',  marker_size=2)
        PDCSAP_traces['SAP_trace_' + str(x)]=go.Scattergl(x=data2plot[3][x], name=f"Quarter {lc_collection[x].quarter}", y=data2plot[0][x], mode='markers',  marker_size=2)
        norm_traces['SAP_trace_' + str(x)]=go.Scattergl(x=data2plot[3][x], name=f"Quarter {lc_collection[x].quarter}", y=data2plot[2][x], mode='markers',  marker_size=2)
    return(PDCSAP_traces, SAP_traces, norm_traces, fully_norm_flux_trace)


In [94]:
test2=lightcurve_traces(lc_collection)

In [95]:
len(test2[0])

16

In [96]:
def lightcurve_plot(data):
    
    traces2plot=lightcurve_traces(data)

    flux_unit=data[0]['flux'].unit.to_string()
    time_unit=data[0]['time'].format

    lc_name=data[0].meta['OBJECT']

    t_ini_limit=float(data[0].meta['TSTART'])
    t_fin_limit=float(data[len(data)-1].meta['TSTOP'])

    PDCSAP_fig_data, SAP_fig_data=list(traces2plot[0].values()), list(traces2plot[1].values())
    norm_fig_data, fully_norm_flux_fig_data=list(traces2plot[2].values()),traces2plot[3]
    
    layout=go.Layout(xaxis=dict(range=[t_ini_limit-20, t_fin_limit+20], autorange=False, zeroline=False),
                  hovermode=False)
    
    PDCSAP_fig, SAP_fig=go.Figure(PDCSAP_fig_data, layout), go.Figure(SAP_fig_data, layout)
    norm_fig, fully_norm_flux_fig=go.Figure(norm_fig_data, layout), go.Figure(fully_norm_flux_fig_data, layout)
    
    PDCSAP_fig.update_layout(title={
        'text': f"{lc_name}'s PDCSAP Lightcurve",
        'y':0.9,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'}, yaxis_title=f"PDCSAP Flux [{flux_unit}]",
                              xaxis_title=f"Days [{time_unit}]", legend_title="Observation Quarters")
    
    SAP_fig.update_layout(title={
        'text': f"{lc_name}'s SAP Lightcurve",
        'y':0.9,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'}, yaxis_title=f"PDCSAP Flux [{flux_unit}]",
                              xaxis_title=f"Days [{time_unit}]", legend_title="Observation Quarters")
    
    norm_fig.update_layout(title={
        'text': f"{lc_name}'s Normalized Lightcurve",
        'y':0.9,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'}, yaxis_title=f"Normalized Flux",
                              xaxis_title=f"Days [{time_unit}]", legend_title="Observation Quarters")
    
    fully_norm_flux_fig.update_layout(title={
       'text': f"{lc_name}'s Normalized and Flattened Lightcurve",
        'y':0.9,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'}, yaxis_title=f"Normalized Flux",
                              xaxis_title=f"Days [{time_unit}]")
    
    return(PDCSAP_fig, SAP_fig, norm_fig, fully_norm_flux_fig)

In [97]:
test3=lightcurve_plot(lc_collection)

In [98]:
test3[1].show()

In [99]:
test3[3].show()

In [43]:
period = np.linspace(1, 40, 25000)
bls = test1[6].to_periodogram(method='bls', period=period, frequency_factor=500)

In [44]:
planet_b_period = bls.period_at_max_power
planet_b_t0 = bls.transit_time_at_max_power
planet_b_dur = bls.duration_at_max_power

In [45]:
folded_lc=test1[6].fold(period=planet_b_period*2, epoch_time=planet_b_t0)
folded_lc_df=folded_lc.to_pandas().reset_index() 
folded_lc_df

time      flux  flux_err                 time_original  quality  \
0     -10.160684  0.998533  0.000301 2011-02-22 03:58:28.529315586        0   
1     -10.160628  0.998433  0.000311 2012-06-23 21:05:12.157882378        0   
2     -10.160375  0.998011  0.000304 2012-09-13 03:56:40.427104463        0   
3     -10.160185  0.998159  0.000302 2011-01-12 12:33:38.431128468        0   
4     -10.160008  0.998045  0.000306 2012-08-03 12:31:38.918367061        0   
...          ...       ...       ...                           ...      ...   
54273  10.158451  0.997933  0.000302 2012-01-13 07:19:41.035122159        0   
54274  10.159477  0.998137  0.000310 2012-05-14 05:37:49.329977129        0   
54275  10.159534  0.998313  0.000297 2009-08-22 11:41:50.143213416        0   
54276  10.159846  0.998026  0.000296 2009-07-12 20:16:43.857675707        0   
54277  10.160173  0.998386  0.000307 2011-12-03 15:56:36.612988785        0   

       timecorr  centroid_col  centroid_row  cadenceno      sap_flux  ...  \
0     -0.001608    777.894395    915.304258      32923  23828.388672  ...   
1      0.002256    946.374315    744.181015      56791  29614.794922  ...   
2      0.003163    775.569280    919.528412      60769  20853.869141  ...   
3     -0.001429    777.884768    915.304318      30934  24026.166016  ...   
4      0.003223    775.573788    919.546026      58780  21104.292969  ...   
...         ...           ...           ...        ...           ...  ...   
54273 -0.001289    777.909395    915.300073      48835  24577.453125  ...   
54274  0.000682    946.358796    744.183453      54802  28973.949219  ...   
54275  0.003160    775.579452    919.493082       6071  21157.839844  ...   
54276  0.003149    775.575658    919.485926       4082  20876.371094  ...   
54277  0.000097    948.877288    748.534602      46846  17981.392578  ...   

       psf_centr1  psf_centr1_err  psf_centr2  psf_centr2_err  mom_centr1  \
0             NaN             NaN         NaN             NaN  777.894395   
1             NaN             NaN         NaN             NaN  946.374315   
2             NaN             NaN         NaN             NaN  775.569280   
3             NaN             NaN         NaN             NaN  777.884768   
4             NaN             NaN         NaN             NaN  775.573788   
...           ...             ...         ...             ...         ...   
54273         NaN             NaN         NaN             NaN  777.909395   
54274         NaN             NaN         NaN             NaN  946.358796   
54275         NaN             NaN         NaN             NaN  775.579452   
54276         NaN             NaN         NaN             NaN  775.575658   
54277         NaN             NaN         NaN             NaN  948.877288   

       mom_centr1_err  mom_centr2  mom_centr2_err  pos_corr1  pos_corr2  
0            0.000150  915.304258        0.000163   0.002569   0.000377  
1            0.000163  744.181015        0.000177   0.005025   0.035509  
2            0.000156  919.528412        0.000178  -0.010440  -0.007867  
3            0.000150  915.304318        0.000161  -0.004929   0.009153  
4            0.000154  919.546026        0.000178   0.004584   0.002845  
...               ...         ...             ...        ...        ...  
54273        0.000148  915.300073        0.000160  -0.007211   0.008863  
54274        0.000166  744.183453        0.000181   0.000115   0.000246  
54275        0.000155  919.493082        0.000177  -0.006122  -0.001445  
54276        0.000156  919.485926        0.000178  -0.022175   0.002640  
54277        0.000184  748.534602        0.000202  -0.000594   0.011483  

[54278 rows x 26 columns]

In [46]:
def relative_height(data, m=1.):
     
     # modified the reject outliers definition from this link https://stackoverflow.com/questions/11686720/is-there-a-numpy-builtin-to-reject-outliers-from-a-list
     #trying to average out the noise in the signal so i can get a decent relative height to measure the widths of the peaks
     
     max_peak=max(data)

     d = np.abs(data - np.median(data))
     mdev = np.median(d)
     s = d/mdev if mdev else np.zeros(len(d))
     
     average=np.average(data[s<m])

     relat_height=float((1-average/max_peak))

     return(relat_height)




def easy_find_peaks(data):

     max_power=max(data)
     
     
     indices = find_peaks(data,  height=[max(data)*0.1, max(data)])[0]
     
     max_peak_index=int(data[data==max_power].index.to_numpy())

     
     other_peak_indices=np.delete(indices,np.where(indices==max_peak_index))
     
     return(max_peak_index, other_peak_indices)






 
     

In [47]:
bls_df=bls.to_table().to_pandas()
test3a=easy_find_peaks(bls_df['power'])

In [48]:
test3a

(5872, array([ 1530,  2616,  3701,  9129, 12385, 15642, 18899]))

In [49]:
test3a[1]

array([ 1530,  2616,  3701,  9129, 12385, 15642, 18899])

In [50]:
test3a[1][1]

2616

In [51]:
def lightcurve_bls(data, period):

    initial_data=lightcurve_data(data)
    stitched=initial_data[6]

    bls_period = np.linspace(1, period, 15000)
    bls=stitched.to_periodogram(method='bls', period=bls_period, frequency_factor=500)

    planet_period = bls.period_at_max_power
    planet_t0 = bls.transit_time_at_max_power
    planet_dur = bls.duration_at_max_power

    lc_name=data[0].meta['OBJECT']

    time_unit=bls.to_table()['period'].unit
    bls_df=bls.to_table().to_pandas()
    
    peak_indices=easy_find_peaks(bls_df['power'])

    max_peak_index, op_indices=peak_indices[0], peak_indices[1]



        
    data_bls=go.Scattergl(x=bls_df['period'], y=bls_df['power'], mode='lines', line=dict(color='black', width=1.5),
                          showlegend=False)
    layout_bls=go.Layout(xaxis=dict(range=[bls_df['period'][0], bls_df['period'][len(bls_df)-1]], autorange=False, zeroline=False),
                hovermode=False)
    fig=go.Figure(data=data_bls, layout=layout_bls)
    
    fig.add_trace(go.Scatter(
        x=[bls_df['period'][j] for j in op_indices],
        y=[bls_df['power'][j] for j in op_indices],
    mode='markers',
    marker=dict(
        size=6,
        color='red',
        symbol='cross'
    ),
    name='Other Significant Peaks'
    ))
    
    fig.add_trace(go.Scatter(
        x=[bls_df['period'][max_peak_index]], 
        y=[bls_df['power'][max_peak_index]],
        
        mode='markers',
        marker=dict(
            size=6,
            color='green',
            symbol='cross'
            ),
        name='Maximum Peak'
        ))
    
   


    fig.update_layout(title={
       'text': f"{lc_name}'s BLS Periodogram",
        'y':0.9,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'},yaxis_title=f" BLS Power", xaxis_title=f" days [{time_unit}]")
    
    fig.data = (fig.data[0],fig.data[1],fig.data[2])
    
    return(fig, planet_period, planet_t0, planet_dur)


    
    

In [52]:
test4=lightcurve_bls(lc_collection, 8)

In [53]:
test4[0].show()